In [1]:
import pandas as pd
import json
import folium

In [2]:
pop_2019 = pd.read_csv('./datasets/Chicago_Population_Counts.csv', usecols = [0,1,2,3], skiprows=61)

In [3]:
pop_2019.drop(columns=['Citywide', '2019'], inplace=True)
pop_2019.columns=['zip', 'pop']

In [4]:
with open('./datasets/zip_codes.geojson') as f:
    zips_map = json.load(f)

In [5]:
#checking that the zips are the same
geojson_zips = sorted([int(zips_map['features'][i]['properties']['zip']) for i in range(len(zips_map['features']))])
pop_zips = pop_2019['zip']
set(geojson_zips) ^ set(pop_zips)

set()

In [6]:
pop_2019.loc[:, 'zip'] = pop_2019['zip'].astype(str)

In [7]:
with open('./datasets/CTA_RailLines.geojson') as f:
    rail_map = json.load(f)
with open('./datasets/CTA_BusRoutes.geojson') as f:
    bus_route_map = json.load(f)

In [8]:
quantiles = list(pop_2019['pop'].quantile([0,0.25,0.5,0.75,0.98,1]))

m = folium.Map(location=[41.881832, -87.623177], tiles='openstreetmap', zoom_start=10)

folium.Choropleth(
    geo_data=zips_map,
    data=pop_2019,
    columns=['zip', 'pop'],
    key_on='properties.zip',
    name='Population',
    fill_color='YlGn',
    fill_opacity=0.7,
    line_opacity=0.3,
    bins=quantiles,
    legend_name=f'Population by ZIP Code in 2019',
).add_to(m)

folium.GeoJson(rail_map, name='Train Lines').add_to(m)

folium.GeoJson(bus_route_map, name='Bus Routes', show=False).add_to(m)

folium.LayerControl().add_to(m)

m.save(f'population_with_transit_lines.html')

In [9]:
m